In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import pandas as pd
from sklearn.metrics.pairwise import cosine_similarity
import scoring

In [3]:
resumes = pd.read_parquet('processed/resume_embeddings.parquet')

In [4]:
jobs = pd.read_parquet('processed/dice_job_descriptions_embeddings.parquet')

In [10]:
resumes

ID                                         Resume_str  \
0     16852973           HR ADMINISTRATOR/MARKETING ASSOCIATE\...   
1     22323967           HR SPECIALIST, US HR OPERATIONS      ...   
2     33176873           HR DIRECTOR       Summary      Over 2...   
3     27018550           HR SPECIALIST       Summary    Dedica...   
4     17812897           HR MANAGER         Skill Highlights  ...   
...        ...                                                ...   
2479  99416532           RANK: SGT/E-5 NON- COMMISSIONED OFFIC...   
2480  24589765           GOVERNMENT RELATIONS, COMMUNICATIONS ...   
2481  31605080           GEEK SQUAD AGENT         Professional...   
2482  21190805           PROGRAM DIRECTOR / OFFICE MANAGER    ...   
2483  37473139           STOREKEEPER II       Professional Sum...   

                                            Resume_html  Category  \
0     <div class="fontsize fontface vmargins hmargin...        HR   
1     <div class="fontsize fontface vmargins hmargin...        HR   
2     <div class="fontsize fontface vmargins hmargin...        HR   
3     <div class="fontsize fontface vmargins hmargin...        HR   
4     <div class="fontsize fontface vmargins hmargin...        HR   
...                                                 ...       ...   
2479  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2480  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2481  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2482  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2483  <div class="fontsize fontface vmargins hmargin...  AVIATION   

                                       extracted_skills  length  \
0     [Accounting, Ads, Advertising, Analytical skil...    5442   
1     [Adobe Photoshop, ADP, Asset Management, brand...    5572   
2     [Recruiting, FMLA/EEO/FLSA, HRIS Development, ...    7720   
3     [Type 50 wpm and 10-Key by touch, Microsoft pr...    2855   
4     [ADA, ADP, art, agency, benefits, Benefits Adm...    9172   
...                                                 ...     ...   
2479  [Secret Clearance, Stock Control, Management, ...    5533   
2480  [arbitration, agency, budgets, Budget, continu...    7108   
2481  [Active Directory, Hardware, Customer Service,...    2020   
2482  [Adobe, CPR, Customer Service, Customer Care, ...    5074   
2483  [Architectural Drafting, AutoCAD, Customer Ser...    5234   

                                         matched_skills  \
0     [accounting, create advertisements, outdoor ad...   
1     [Adobe Photoshop, asset management, maintain c...   
2     [recruit members, foreign affairs policy devel...   
3     [personnel management, customer service, resol...   
4     [create artwork, coaching techniques, coaching...   
...                                                 ...   
2479  [follow stock control instructions, operations...   
2480  [examine budgets, update budget, continuous im...   
2481  [hardware materials, customer service, manage ...   
2482  [customer service, maintain customer service, ...   
2483  [create architectural sketches, customer servi...   

                                             embeddings  
0     [-0.051119804, 0.051380936, -0.1956489, -0.000...  
1     [-0.013715399, 0.01982399, -0.15967667, 0.0198...  
2     [-0.037161566, 0.0036097213, -0.19848743, -0.0...  
3     [-0.004071229, -0.0062129777, -0.16848274, -0....  
4     [0.008319367, 0.02057786, -0.17201392, 0.01393...  
...                                                 ...  
2479  [0.0049826736, 0.0045687603, -0.19545835, -0.0...  
2480  [0.04153785, 0.038161203, -0.16648234, -0.0115...  
2481  [0.010476048, 0.028934365, -0.16972545, 0.0036...  
2482  [-0.013092378, 0.055586472, -0.17801957, -0.01...  
2483  [-0.036120985, 0.033106253, -0.17913961, -0.03...  

[2484 rows x 8 columns]

In [6]:
print(resumes['matched_skills'].iloc[0])

['accounting' 'create advertisements' 'outdoor advertising'
 'monitor billing procedures' 'manage budgets' 'customer service'
 'perform data analysis' 'documentation types' 'financial management'
 'maintain relationships with government agencies' 'hire human resources'
 'types of insurance' 'store design layout' 'services marketing'
 'medical terminology' 'office administration' 'manage payroll'
 'recruit personnel' 'company policies' 'hang advertising posters'
 'conduct public presentations' 'public relations' 'statistics'
 'manage website']


In [7]:
jobs

advertiserurl  \
0      https://www.dice.com/jobs/detail/AUTOMATION-TE...   
1      https://www.dice.com/jobs/detail/Information-S...   
2      https://www.dice.com/jobs/detail/Business-Solu...   
3      https://www.dice.com/jobs/detail/Java-Develope...   
4      https://www.dice.com/jobs/detail/DevOps-Engine...   
...                                                  ...   
21995  https://www.dice.com/jobs/detail/Web-Designer-...   
21996  https://www.dice.com/jobs/detail/Senior-Front-...   
21997  https://www.dice.com/jobs/detail/QA-Analyst-Sa...   
21998  https://www.dice.com/jobs/detail/Tech-Lead%252...   
21999  https://www.dice.com/jobs/detail/C%2526%252347...   

                                 company  \
0      Digital Intelligence Systems, LLC   
1      University of Chicago/IT Services   
2                   Galaxy Systems, Inc.   
3                          TransTech LLC   
4                       Matrix Resources   
...                                  ...   
21995                     IAC Publishing   
21996                Omega Solutions Inc   
21997          San Francisco Health Plan   
21998                     IAC Publishing   
21999          Technology Resource Group   

                                employmenttype_jobstatus  \
0      C2H Corp-To-Corp, C2H Independent, C2H W2, 3 M...   
1                                              Full Time   
2                                              Full Time   
3                                              Full Time   
4                                              Full Time   
...                                                  ...   
21995                                          Full Time   
21996                                          Full Time   
21997                                          Full Time   
21998                                          Full Time   
21999                               Full Time, Full Time   

                                          jobdescription               jobid  \
0      Looking for Selenium engineers...must have sol...  Dice Id : 10110693   
1      The University of Chicago has a rapidly growin...  Dice Id : 10114469   
2      GalaxE.SolutionsEvery day, our solutions affec...  Dice Id : CXGALXYS   
3      Java DeveloperFull-time/direct-hireBolingbrook...  Dice Id : 10113627   
4      Midtown based high tech firm has an immediate ...  Dice Id : matrixga   
...                                                  ...                 ...   
21995   Company Description We are searching for a ta...  Dice Id : 10112803   
21996   CONTACT - priya@omegasolutioninc.com / 408-45...  Dice Id : 10289500   
21997  Do you take pride in your work knowing that th...  Dice Id : 10115761   
21998  Company Description What We Can Offer YouAs th...  Dice Id : 10112803   
21999  Experience in C/C++ ProgrammingDevelopment exp...  Dice Id : 90734436   

      joblocation_address                                           jobtitle  \
0             Atlanta, GA                           AUTOMATION TEST ENGINEER   
1             Chicago, IL                      Information Security Engineer   
2          Schaumburg, IL                       Business Solutions Architect   
3         Bolingbrook, IL  Java Developer (mid level)- FT- GREAT culture,...   
4             Atlanta, GA                                    DevOps Engineer   
...                   ...                                                ...   
21995         Oakland, CA                                       Web Designer   
21996   San Francisco, CA  Senior Front End Web Developer - Full Time at ...   
21997   San Francisco, CA                                         QA Analyst   
21998         Oakland, CA                               Tech Lead-Full Stack   
21999     Santa Clara, CA                                   C/C++ Programmer   

             postdate                                            shift  \
0          1 hour ago  Telecommuting not available|Travel not required   
1 

In [6]:
resumes['Category'].value_counts()

Category
INFORMATION-TECHNOLOGY    120
BUSINESS-DEVELOPMENT      120
ADVOCATE                  118
CHEF                      118
ENGINEERING               118
ACCOUNTANT                118
FINANCE                   118
FITNESS                   117
AVIATION                  117
SALES                     116
BANKING                   115
HEALTHCARE                115
CONSULTANT                115
CONSTRUCTION              112
PUBLIC-RELATIONS          111
HR                        110
DESIGNER                  107
ARTS                      103
TEACHER                   102
APPAREL                    97
DIGITAL-MEDIA              96
AGRICULTURE                63
AUTOMOBILE                 36
BPO                        22
Name: count, dtype: int64

In [7]:
resumes[resumes['Category']=='INFORMATION-TECHNOLOGY']

ID                                         Resume_str  \
217  36856210           INFORMATION TECHNOLOGY         Summar...   
218  21780877           INFORMATION TECHNOLOGY SPECIALIST\tGS...   
219  33241454           INFORMATION TECHNOLOGY SUPERVISOR    ...   
220  25990239           INFORMATION TECHNOLOGY INSTRUCTOR    ...   
221  16899268           INFORMATION TECHNOLOGY MANAGER/ANALYS...   
..        ...                                                ...   
332  27485716           CORPORATE PROJECT MANAGER       Caree...   
333  26480367           IT TECHNOLOGY SPECIALIST       Profes...   
334  81761658           IT MANAGER             Highlights    ...   
335  79541391           SUBJECT MATTER EXPERT (INFORMATION TE...   
336  23666211           TRAINING MANAGER         Executive Su...   

                                           Resume_html  \
217  <div class="fontsize fontface vmargins hmargin...   
218  <div class="fontsize fontface vmargins hmargin...   
219  <div class="fontsize fontface vmargins hmargin...   
220  <div class="fontsize fontface vmargins hmargin...   
221  <div class="fontsize fontface vmargins hmargin...   
..                                                 ...   
332  <div class="fontsize fontface vmargins hmargin...   
333  <div class="fontsize fontface vmargins hmargin...   
334  <div class="fontsize fontface vmargins hmargin...   
335  <div class="fontsize fontface vmargins hmargin...   
336  <div class="fontsize fontface vmargins hmargin...   

                   Category  \
217  INFORMATION-TECHNOLOGY   
218  INFORMATION-TECHNOLOGY   
219  INFORMATION-TECHNOLOGY   
220  INFORMATION-TECHNOLOGY   
221  INFORMATION-TECHNOLOGY   
..                      ...   
332  INFORMATION-TECHNOLOGY   
333  INFORMATION-TECHNOLOGY   
334  INFORMATION-TECHNOLOGY   
335  INFORMATION-TECHNOLOGY   
336  INFORMATION-TECHNOLOGY   

                                      extracted_skills  length  \
217  [Enterprise platforms, Product Lifecycle Manag...    4888   
218  [budget, cabling, cisco, hardware, Client, doc...    6491   
219  [Army, Cisco, counseling, customer assistance,...    4447   
220  [Data Analysis, Curriculum design, Advanced Da...    6443   
221  [Project management, Program management, Proce...    4203   
..                                                 ...     ...   
332  [Strategic Planning, Visioning & Tactical Exec...    6358   
333  [TCP/IP, Network monitoring and tools, storage...    5296   
334  [Antivirus, Backup Exec, Backup, budget, Cisco...    6956   
335  [SAP, HP ALM, Network Configuration, Database ...   13149   
336  [Training and Development, Supervision and tra...    6237   

                                        matched_skills  \
217  [Microsoft Visio, establish collaborative rela...   
218  [update budget, Cisco, hardware materials, cou...   
219  [Cisco, assist customers, database, documentat...   
220  [perform data analysis, advise on curriculum d...   
221  [project management, program management, ident...   
..                                                 ...   
332  [strategic planning, apply change management, ...   
333  [network management system tools, manage stora...   
334  [perform backups, update budget, Cisco, Cisco,...   
335  [analyse network configuration and performance...   
336  [develop training programmes, advise on curric...   

                                            embeddings  
217  [0.024866175, 0.003601386, -0.18570414, -0.008...  
218  [-0.010633438, 0.007611083, -0.17417881, 0.006...  
219  [-0.037932523, 0.037896443, -0.17501546, 0.010...  
220  [-0.03240509, -0.00092515495, -0.15758836, -0....  
221  [0.0091975955, 0.015827738, -0.15481094, -0.00...  
..                                                 ...  
332  [-0.0005144458, 0.01685918, -0.19226903, 0.010...  
333  [-0.021583611, 0.039958835, -0.14052038, 0.021...  
334  [-0.014514066, 0.028190823, -0.18224227, 0.004...  
335  [-0.026711699, 0.010593939, -0.18707459, -0.04...  
336  [-

In [8]:
job_embeddings = jobs['embeddings'].tolist()

In [9]:
resume = resumes.iloc[90]

In [10]:
embedding = resume['embeddings']

In [11]:
print(resume['matched_skills'])

['use microsoft office' 'counsel clients' 'customer service'
 'manage payroll' 'manage human resources' 'hire human resources'
 'criminal law' 'real estate market']


In [12]:
distances = cosine_similarity([embedding], job_embeddings)

In [13]:
distances.max()

np.float64(0.8545799251550326)

In [14]:
distances.argmax()

np.int64(18145)

In [15]:
def get_metrics(list1, list2):
    set1 = set(list1)
    set2 = set(list2)

    overlap = set1 & set2
    difference = set1 ^ set2

    print(f"Overlap: {len(overlap)}")
    print(f"No Overlap: {len(difference)} ")

In [16]:
resume['matched_skills']

array(['use microsoft office', 'counsel clients', 'customer service',
       'manage payroll', 'manage human resources', 'hire human resources',
       'criminal law', 'real estate market'], dtype=object)

In [17]:
jobs['matched_skills'].iloc[distances.argmax()]

array(['use microsoft office', 'Microsoft Access', 'listen actively',
       'solve problems', 'communication', 'perform data analysis',
       'perform multiple tasks at the same time', 'customer service',
       'manage time', 'manage teamwork', 'tolerate stress',
       'meet deadlines', 'ethics', 'information confidentiality'],
      dtype=object)

In [ ]:
[[1],[2],[3]]
[[4],[5],[6],[7]]

In [18]:
get_metrics(resume['matched_skills'], jobs['matched_skills'].iloc[distances.argmax()])

Overlap: 2
No Overlap: 18 


In [11]:
resumes_10 = resumes.sample(n=10, random_state=42)

In [12]:
resumes_10

ID                                         Resume_str  \
420   99244405             Kpandipou    Koffi         Summary ...   
1309  17562754           DIRECTOR OF DIGITAL TRANSFORMATION   ...   
2023  30311725           SENIOR PROJECT MANAGER       Professi...   
1360  19007667           CHEF       Summary     Experienced ca...   
2186  11065180           OPERATIONS MANAGER       Summary    E...   
602   39237915           BUSINESS DEVELOPMENT MANAGER       Pr...   
173   17199951           JOB CAPTAIN\nDESIGNER         Highlig...   
599   18236085           DIRECTOR OF BUSINESS DEVELOPMENT     ...   
435   79663360           SUBSTITUTE TEACHER       Professional...   
188   62312955        R        GRAPHIC ARTIST, DESIGNER       ...   

                                            Resume_html              Category  \
420   <div class="RNA skn-rbn1 fontsize fontface vma...               TEACHER   
1309  <div class="fontsize fontface vmargins hmargin...         DIGITAL-MEDIA   
2023  <div class="fontsize fontface vmargins hmargin...          CONSTRUCTION   
1360  <div class="fontsize fontface vmargins hmargin...                  CHEF   
2186  <div class="fontsize fontface vmargins hmargin...               BANKING   
602   <div class="fontsize fontface vmargins hmargin...  BUSINESS-DEVELOPMENT   
173   <div class="fontsize fontface vmargins hmargin...              DESIGNER   
599   <div class="fontsize fontface vmargins hmargin...  BUSINESS-DEVELOPMENT   
435   <div class="fontsize fontface vmargins hmargin...               TEACHER   
188   <div class="fontsize fontface vmargins hmargin...              DESIGNER   

                                       extracted_skills  length  \
420   [Superb communication (verbal, written), Relia...    5576   
1309  [Journalism, Editorial, Leadership, New Media,...    6450   
2023  [Advanced problem solving, Project planning an...    5713   
1360  [delivery, Detail oriented, English, inventory...    1483   
2186  [KYC, Anti Money Laundering, legal documentati...    4970   
602   [Inventory Management, Leadership Development,...    5642   
173   [Adobe Illustrator, Photoshop 6.0, premier, Au...    3805   
599   [agency, benefits, brochure, budget, business ...    5536   
435   [Analytical Thinking, Knowledge of child devel...    5325   
188   [Digital Illustration, Graphic Design, Adobe C...    2755   

                                         matched_skills  \
420   [solve problems, advise on career, reinforce p...   
1309  [journalism, leadership principles, conserve n...   
2023  [accounting, team building, strategic planning...   
1360  [English, manage inventory, manage inventory, ...   
2186  [develop documentation in accordance with lega...   
602   [manage inventory, risk management, develop st...   
173   [Adobe Illustrator, management consulting, cou...   
599   [update budget, align efforts towards business...   
435   [think analytically, communication, make decis...   
188   [use digital illustration techniques, graphic ...   

                                             embeddings  
420   [-0.0043232744, 0.026767537, -0.15574335, 0.02...  
1309  [-0.013330014, 0.02773742, -0.18409428, 0.0039...  
2023  [-0.022575961, 0.02060165, -0.17989965, 0.0278...  
1360  [0.0019199473, -0.0015721761, -0.17656681, 0.0...  
2186  [0.022708356, 0.0071677906, -0.16623847, 0.019...  
602   [-0.013238902, 0.01884628, -0.18273148, 0.0255...  
173   [-0.03396876, 0.054326113, -0.1567637, -0.0149...  
599   [-0.013742949, 0.020884922, -0.18381548, 0.006...  
435   [-0.028129779, 0.021530585, -0.15706235, -0.01...  
188   [-0.03752506, 0.08240038, -0.17028266, 0.00106...

In [16]:
resume_embeddings = resumes['embeddings'].tolist()

In [17]:
job_embeddings = jobs['embeddings'].tolist()

In [19]:
similarities = cosine_similarity(resume_embeddings, job_embeddings)

In [21]:
best_match_indices = similarities.argmax(axis=1)
best_match_scores = similarities.max(axis=1)

In [27]:
resumes['best_match_index'] = best_match_indices
resumes['best_match_score'] = best_match_scores
resumes['best_match_embedding'] = jobs.loc[best_match_indices, 'embeddings'].values
resumes['best_match_skills'] = jobs.loc[best_match_indices, 'matched_skills'].values

In [28]:
resumes

ID                                         Resume_str  \
0     16852973           HR ADMINISTRATOR/MARKETING ASSOCIATE\...   
1     22323967           HR SPECIALIST, US HR OPERATIONS      ...   
2     33176873           HR DIRECTOR       Summary      Over 2...   
3     27018550           HR SPECIALIST       Summary    Dedica...   
4     17812897           HR MANAGER         Skill Highlights  ...   
...        ...                                                ...   
2479  99416532           RANK: SGT/E-5 NON- COMMISSIONED OFFIC...   
2480  24589765           GOVERNMENT RELATIONS, COMMUNICATIONS ...   
2481  31605080           GEEK SQUAD AGENT         Professional...   
2482  21190805           PROGRAM DIRECTOR / OFFICE MANAGER    ...   
2483  37473139           STOREKEEPER II       Professional Sum...   

                                            Resume_html  Category  \
0     <div class="fontsize fontface vmargins hmargin...        HR   
1     <div class="fontsize fontface vmargins hmargin...        HR   
2     <div class="fontsize fontface vmargins hmargin...        HR   
3     <div class="fontsize fontface vmargins hmargin...        HR   
4     <div class="fontsize fontface vmargins hmargin...        HR   
...                                                 ...       ...   
2479  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2480  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2481  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2482  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2483  <div class="fontsize fontface vmargins hmargin...  AVIATION   

                                       extracted_skills  length  \
0     [Accounting, Ads, Advertising, Analytical skil...    5442   
1     [Adobe Photoshop, ADP, Asset Management, brand...    5572   
2     [Recruiting, FMLA/EEO/FLSA, HRIS Development, ...    7720   
3     [Type 50 wpm and 10-Key by touch, Microsoft pr...    2855   
4     [ADA, ADP, art, agency, benefits, Benefits Adm...    9172   
...                                                 ...     ...   
2479  [Secret Clearance, Stock Control, Management, ...    5533   
2480  [arbitration, agency, budgets, Budget, continu...    7108   
2481  [Active Directory, Hardware, Customer Service,...    2020   
2482  [Adobe, CPR, Customer Service, Customer Care, ...    5074   
2483  [Architectural Drafting, AutoCAD, Customer Ser...    5234   

                                         matched_skills  \
0     [accounting, create advertisements, outdoor ad...   
1     [Adobe Photoshop, asset management, maintain c...   
2     [recruit members, foreign affairs policy devel...   
3     [personnel management, customer service, resol...   
4     [create artwork, coaching techniques, coaching...   
...                                                 ...   
2479  [follow stock control instructions, operations...   
2480  [examine budgets, update budget, continuous im...   
2481  [hardware materials, customer service, manage ...   
2482  [customer service, maintain customer service, ...   
2483  [create architectural sketches, customer servi...   

                                             embeddings  best_match_index  \
0     [-0.051119804, 0.051380936, -0.1956489, -0.000...              6304   
1     [-0.013715399, 0.01982399, -0.15967667, 0.0198...              2643   
2     [-0.037161566, 0.0036097213, -0.19848743, -0.0...             16469   
3     [-0.004071229, -0.0062129777, -0.16848274, -0....             21520   
4     [0.008319367, 0.02057786, -0.17201392, 0.01393...              4296   
...                                                 ...               ...   
2479  [0.0049826736, 0.0045687603, -0.19545835, -0.0...              6742   
2480  [0.04153785, 0.038161203, -0.16648234, -0.0115...              2634   
2481  [0.010476048, 0.028934365, -0.16972545, 0.0036...             19056   
2482  [-0.013092378, 0.055586472, -0.17801957, -0.01...             10

In [29]:
resumes['best_match_score'].mean()

np.float64(0.8267800212805207)

In [32]:
scoring.intersection_score(resumes['matched_skills'], resumes['best_match_skills'])

0.1467325375768066